In [1]:
import requests
from tqdm import tnrange, tqdm_notebook
from netCDF4 import Dataset
from bokeh.plotting import figure, show
from bokeh.io import output_notebook

In [2]:
def download_file(doi):
    #We indicate with the header that we want a netcdf file, not a HTML page
    headers = {'Accept':'application/x-netcdf'}
    r = requests.get(doi,headers=headers,stream=True)
    #Set file name
    fname = doi.split('/')[-1]+'.nc'
    #Download file with progress bar
    if r.status_code == 403:
        print("File Unavailable")
    if 'content-length' not in r.headers:
        print("Did not get file")
    else:
        with open(fname, 'wb') as f:
            total_length = int(r.headers.get('content-length'))
            pbar = tnrange(int(total_length/1024), unit="B")
            for chunk in r.iter_content(chunk_size=1024):
                if chunk:
                    pbar.update()
                    f.write(chunk)
        return fname

In [3]:
#Download data
doi = 'https://doi.org/10.14291/tccon.ggg2014.parkfalls01.R1'
park_falls = download_file(doi)
doi = 'https://doi.org/10.14291/tccon.ggg2014.ascension01.R0/1149285'
ascension = download_file(doi)

In [5]:
output_notebook()

park_falls_data = Dataset(park_falls, "r")
ascension_data = Dataset(ascension, "r")

# set up figure
p = figure(title="CO2 Concentration from TCCON Sites", \
           x_axis_label='Time',y_axis_label='CO2 (ppm)', \
           tools=['zoom_in','zoom_out','wheel_zoom','pan','undo','redo','reset','save','help'],\
           active_scroll='wheel_zoom')

# add lines
p.line(park_falls_data['time'][:], park_falls_data['xco2_ppm'][:],legend='Park Falls')
p.line(ascension_data['time'][:], ascension_data['xco2_ppm'][:],legend='Ascension',line_color='orange')

# make things interactive
p.legend.location = "top_left"
p.legend.click_policy = "hide"

show(p)


Loading BokehJS ...